In [1]:
import folium
import pandas as pd
import branca

In [13]:
#read csv with bus data
df = pd.read_csv('../data/vehicle-position-matched-offline-20180813.csv')

#split the linkref into wayid, source and target columns
df['wayId'], df['source'], df['target'] = df['LinkRef'].str.split(':').str

#Convert time column to datetime
df['Time'] = pd.to_datetime(df['Time'])
#Set timestamp to index, allowing for interval aggregation
df = df.set_index('Time')
#Remove data during the night for now
df = df.between_time('06:00','21:00')

#group the data by wayId and calculate the mean and count
df_agg = df.groupby('wayId', as_index=False)['Speed'].agg({"mean","count"}).reset_index()

df_agg.head()

wayId  count       mean
0  103524893   3133  11.840511
1  103524901    107   0.904766
2  103524902  12149   7.546960
3  108233932    742   6.959569
4  108233935   1022   5.379354

In [14]:
df_5min = df.groupby([pd.Grouper(freq='5Min'),'wayId']).size().reset_index(name='count')
df_5min.head()

Time      wayId  count
0 2018-08-13 06:00:00  103524893     41
1 2018-08-13 06:00:00  103524901      1
2 2018-08-13 06:00:00  103524902    150
3 2018-08-13 06:00:00  108233932      8
4 2018-08-13 06:00:00  108233935      8

In [35]:
#Create two colormaps, one for the mean speed and one for the number of meassurements
cm_mean = branca.colormap.linear.YlOrRd_04.scale(0,df_agg['mean'].max())
cm_count = branca.colormap.linear.YlOrRd_04.scale(0,df_agg['count'].max())


#Create a map object in valby
m = folium.Map(location=[55.6691591,12.5103835], zoom_start=16)


#Define two style functions, that change the color depending on the value of the mean speed/count
def style_trafic_mean(feature):
    wayid = feature['properties']['WayId']
    val = df_agg[df_agg['wayId']==str(wayid)]['mean']
    if len(val)==0:
        val = 0
    else:
        val = val.values[0]
        
    return {
            'fillOpacity': 0.5,
            'weight': 10,
            'color':cm_mean(val)
        }

def style_trafic_count(feature):
    wayid = feature['properties']['WayId']
    val = df_agg[df_agg['wayId']==str(wayid)]['count']
    if len(val)==0:
        val = 0
    else:
        val = val.values[0]
    
    return {
            'fillOpacity': 0.5,
            'weight': 10,
            'color':cm_count(val)
    }




#Add the geojson with colors
g=folium.GeoJson('../data/road_network.geojson',name='mean speed', style_function=style_trafic_mean)
folium.GeoJsonTooltip(['WayId']).add_to(g)
g.add_to(m)
#This is a hack to show a colorbar, and also include all the streets
m.choropleth(geo_data='../data/road_network.geojson'
             , data=df_agg, columns=['wayId','mean']
             , key_on='feature.properties.WayId'
             , fill_color='YlOrRd'
             , name='Streets'
             , legend_name='Mean speed [m/s]')
#Add a control layer to our map
folium.LayerControl().add_to(m)

#Show the resulting map
m


In [36]:
#Do the same as before, but now look at the meassurement density instead

m2 = folium.Map(location=[55.6691591,12.5103835], zoom_start=16)

g2=folium.GeoJson('../data/road_network.geojson',name='measurement density', style_function=style_trafic_count)
folium.GeoJsonTooltip(['WayId']).add_to(g2)
g2.add_to(m2)

m2.choropleth(geo_data='../data/road_network.geojson'
             , data=df_agg, columns=['wayId','count']
             , key_on='feature.properties.WayId'
             , fill_color='YlOrRd'
             , name='Streets'
             , legend_name='Meassurements ')

folium.LayerControl().add_to(m2)

m2

In [38]:


df_5min_agg = df_5min.groupby('wayId', as_index=False)['count'].agg({"mean","min"}).reset_index()

cm_5min_mean = branca.colormap.linear.YlOrRd_04.scale(0,10)


def style_trafic_5min_avg(feature):
    wayid = feature['properties']['WayId']
    val = df_5min_agg[df_5min_agg['wayId']==str(wayid)]['mean']
    if len(val)==0:
        val = 0
    else:
        val = val.values[0]
    
    return {
            'fillOpacity': 0.5,
            'weight': 10,
            'color':cm_5min_mean(val)
    }

m_5min = folium.Map(location=[55.6691591,12.5103835], zoom_start=16)

g= folium.GeoJson('../data/road_network.geojson',name='mean count', style_function=style_trafic_5min_avg)
folium.GeoJsonTooltip(['WayId']).add_to(g)
g.add_to(m_5min)

m_5min.choropleth(geo_data='../data/road_network.geojson'
                 ,name ='streets'
                 , legend_name=',mean count'
                 , data=df_5min_agg
                 ,columns=['wayId','mean']
                 ,key_on = 'feature.properties.WayId'
                 , fill_color='YlOrRd')



folium.LayerControl().add_to(m_5min)

m_5min

In [39]:
cm_5min_min = branca.colormap.linear.YlOrRd_04.scale(0,df_5min_agg['mean'].max())


def style_trafic_5min_avg(feature):
    wayid = feature['properties']['WayId']
    val = df_5min_agg[df_5min_agg['wayId']==str(wayid)]['mean']
    if len(val)==0:
        val = 0
    else:
        val = val.values[0]
    
    return {
            'fillOpacity': 0.5,
            'weight': 10,
            'color':cm_5min_mean(val)
    }

m_5min = folium.Map(location=[55.6691591,12.5103835], zoom_start=16)

folium.GeoJson('../data/road_network.geojson',name='mean count', style_function=style_trafic_5min_avg).add_to(m_5min)

m_5min.choropleth(geo_data='../data/road_network.geojson'
                 ,name ='legend'
                 , legend_name=',mean count'
                 , data=df_5min_agg
                 ,columns=['wayId','mean']
                 ,key_on = 'feature.properties.WayId'
                 , fill_color='YlOrRd')



folium.LayerControl().add_to(m_5min)

m_5min

In [131]:
styledict={}

for name, group in df_5min.groupby('wayId'):
    df = pd.DataFrame({'colorr':group['count'].apply(cm_5min).tolist()},index=group['Time'].astype(str).tolist())

    #print(df)
    #group['Time'] = group['Time'].astype(str)
    #group = group.set_index('Time')
    #group['color'] = group['count'].apply(cm_5min)
    #print(group)
    #a=group[['count','color']].to_dict()
    styledict[name]=df.to_dict(orient='index')
